## Scenario: **Exploring Potential Oil and Gas Drilling Sites Near Houston's Industrial Development Zone (IDZ)**
*Notebook 5 of 5*

With the increasing global demand for energy, Houston's outskirts have been identified as potential regions for oil and gas exploration. Houston's Industrial Development Division is keen to discover and capitalize on new oil and gas reservoirs. However, to ensure minimal environmental disruption and efficient transportation of resources, these drilling sites must be near the newly proposed Industrial Development Zone (IDZ).

### Objective:

The aim is to identify potential drilling sites within a designated proximity to the IDZ, which is represented as a hexagonal boundary. These potential sites, once identified, will undergo geological and environmental impact assessments.

### Procedure:

**1. Data Collection:**
- Gather geospatial data for potential drilling sites, including their latitudes and longitudes.
- Represent the IDZ’s location using the H3 geospatial indexing system, centered around a specified set of coordinates.

**2. Buffering:**
- Define a buffer zone around the IDZ using H3 cells. This buffer ensures that potential drilling sites are within feasible regions for exploration.
- Any site falling within this buffer can be efficiently connected to the IDZ for logistics.

**3. Spatial Joining:**
- Utilize H3 indexing to identify which potential drilling sites fall within the buffer zone.
- This spatial operation will help pinpoint suitable locations for exploration.

**4. Spatial Autocorrelation Analysis:**
- Apply spatial autocorrelation analysis to detect clusters of potential drilling sites with similar geological features.
- Larger reservoirs may exhibit such clustering, making them strategic choices to meet higher energy demands.

**5. Visualization:**
- Create a map that visualizes the following:
    - The IDZ represented by its H3 hexagonal boundary.
    - The buffer zone around the IDZ.
    - All potential drilling sites identified using H3 indexing.
    - Other relevant features, such as existing infrastructure or environmental factors.




In [1]:
pip install geopandas pandas h3 matplotlib pysal splot shapely pyproj folium keplergl

Note: you may need to restart the kernel to use updated packages.



### Library Imports:
The scenario revolves around geospatial operations. The imported libraries, such as `geopandas`, `pandas`, `pysal`, and `splot`, equip us with the tools needed for a range of operations. These go from basic geospatial data manipulation to advanced spatial autocorrelation analysis.

### WKT Parsing:
The well-known text (WKT) representation is a ubiquitous standard in the geospatial domain. It is used for representing geometric objects in a readable text format. In this context, we use it to parse and derive the geometry of a point. This point can symbolize specific city locations or even represent locations of oil/gas wells.

### Coordinate Transformation:
Different geospatial datasets might be represented in different coordinate reference systems. Transforming coordinates is pivotal to ensure alignment across these datasets. This step is especially crucial when preparing data for specific visualizations or analyses or when integrating with web-based mapping tools.


## Relevance to the Scenario:

### Mock Dataset Creation:
This part creates a mock dataset representing existing wells with their geographical locations and production rates. The wells could be potential freshwater sources for the city's Urban Development Zone (UDZ). The production rate might be used later on to identify high-yielding wells.

The provided code sets up a foundation for the scenario by defining the region of interest (the hexagonal UDZ) and a sample dataset of wells. Further operations, such as buffering, spatial joining, and analysis, can then be performed to meet the objectives of the scenario.


In [16]:
from shapely.geometry import Point
import numpy as np
import random
import folium
import geopandas as gpd
import h3
from shapely.geometry import Polygon

# Define the range for ELAPSETIME
start = 0
stop = 100

# Define the bounding box for 
minx, miny = -103.6806, 30.0195
maxx, maxy = -104.3606, 30.5995
# Generate a list of random lat-long points within the bounding box
points = [Point(random.uniform(minx, maxx), random.uniform(miny, maxy)) for _ in np.arange(10000)]

# Create a geodataframe with the specified columns and attributes
gdf = gpd.GeoDataFrame({'OIL_PRODUCTION_BBL': [random.randint(start, stop) for _ in np.arange(10000)],
                        'geometry': points}, crs='EPSG:4326')
print(gdf)

      OIL_PRODUCTION_BBL                     geometry
0                      0  POINT (-103.71703 30.35631)
1                     84  POINT (-103.91514 30.57588)
2                     90  POINT (-103.88639 30.51815)
3                     41  POINT (-104.12180 30.27523)
4                     39  POINT (-104.29544 30.17879)
...                  ...                          ...
9995                  15  POINT (-103.70655 30.26884)
9996                  50  POINT (-103.98160 30.17421)
9997                 100  POINT (-103.96108 30.51144)
9998                  19  POINT (-104.33921 30.05984)
9999                  26  POINT (-104.07284 30.53348)

[10000 rows x 2 columns]


In [17]:
import folium

# Calculate the center latitude and longitude
center_lat = (miny + maxy) / 2
center_long = (minx + maxx) / 2

# Create a new map
m = folium.Map(location=[center_lat, center_long], zoom_start=10)

# Convert geodataframe to GeoJSON
gjson = gdf.to_json()

# Add GeoJSON data to the map
folium.GeoJson(gjson, name='geojson').add_to(m)

# Display the map
m

In [ ]:

import h3

# x = longitude, y = latitude!!!
res = 10
col = f"H3_{res}"
gdf[col] = gdf.apply(lambda row: str(h3.geo_to_h3(row.geometry.y, row.geometry.x, res)), axis=1)

h3_df = gdf.groupby(col)['ELAPSETIME'].describe().reset_index()

from shapely.geometry import Polygon

def cell_to_shapely(cell):
    coords = h3.h3_to_geo_boundary(cell)
    flipped = tuple(coord[::-1] for coord in coords)
    return Polygon(flipped)

h3_geoms = h3_df[col].apply(lambda x: cell_to_shapely(x))
h3_gdf = gpd.GeoDataFrame(data=h3_df, geometry=h3_geoms, crs=4326)

In [13]:
import folium

# Calculate the center latitude and longitude
center_lat = (miny + maxy) / 2
center_long = (minx + maxx) / 2

# Create a new map
m = folium.Map(location=[center_lat, center_long], zoom_start=10)

# Convert geodataframe to GeoJSON
gjson = h3_gdf.to_json()

# Add GeoJSON data to the map
folium.GeoJson(gjson, name='geojson').add_to(m)

# Display the map
m


## Overview

The code in focus assists in identifying spatial patterns in well productivity, specifically how wells correlate with one another and the UDZ (Urban Development Zone). Visualization of these patterns can guide efficient planning and decision-making for the city's freshwater needs.

### K-nearest Neighbors (KNN) and Spatial Weights

**What it does:**
- Determines the number of neighbors to consider for each data point in the GeoDataFrame `gdf`. This is determined by the minimum of 5 or one less than the total number of points.
- Calculates the k-nearest neighbors spatial weights matrix for the dataset.

**Relevance to the Scenario:**
The spatial weights matrix establishes how each observation in the dataset is spatially related to every other observation. This matrix is vital in spatial analysis, helping identify and quantify patterns or relationships between data points.

### Global Moran's I Statistical Test

**What it does:**
- Performs a Global Moran's I statistical test to gauge spatial autocorrelation. This is based on the production rates of the wells, using the previously defined spatial weights.

**Relevance to the Scenario:**
The analysis helps determine if there's a discernible spatial pattern in the production rates of the wells. For instance, the city can ascertain whether high-producing wells cluster near other high-producing wells or if the distribution is random. This knowledge aids decision-making related to water supply distribution or potential drilling projects.

### Visualization of Well Data and UDZ

**What it does:**
- Initializes a map for visualization.
- Illustrates the wells on the map using colors that represent their production rates.
- Superimposes the boundary of the hexagonal tessellation (UDZ) on the map.

**Relevance to the Scenario:**
Visual data representations provide an immediate understanding of the spatial distribution of well productivity and its relationship with the UDZ. This visual context allows planners to quickly identify the locations of high-yielding wells concerning the UDZ.

### Local Moran's I and Visualization

**What it does:**
- Calculates the Local Moran's I statistic for each well to pinpoint local clusters of similar or differing values.
- Showcases these local patterns on a map.

**Relevance to the Scenario:**
Visualizing the Local Moran's I values allows urban planners to pinpoint clusters of high-yielding wells or possible outliers. Recognizing these clusters is essential for infrastructure planning and ensures efficient water supply distribution to the UDZ.

```


In [ ]:
# Compute spatial weights
k = min(5, len(gdf) - 1)
weights = weights.KNN.from_dataframe(gdf, k=k)

# Spatial Autocorrelation Analysis
moran = esda.Moran(gdf['production_rate'], weights)

# Visualization
fig, ax = plt.subplots(figsize=(10, 10))
gdf.plot(column='production_rate', cmap='coolwarm', legend=True, ax=ax)
hexagon.boundary.plot(ax=ax, color='black', linewidth=1)
ax.set_title('Well Production with Hexagonal Tessellation')
plt.show()

# Visualize Local Moran's I
local_moran = esda.Moran_Local(gdf['production_rate'], weights)
plot_local_autocorrelation(local_moran, gdf, 'production_rate')
plt.show()

## Relevance to the Scenario:

### Spatial Joining:
Spatial joining is a process of combining datasets based on their spatial relationship. In this context, we're identifying which of the existing wells are located within the buffered region around the UDZ. By doing this, the city can pinpoint specific wells that are optimal for providing water to the new infrastructures within or near the UDZ.

### Visualization:
Visualization is a powerful tool for urban planning. The map created here depicts the UDZ, the extended (buffered) area around it, all the existing wells, and specifically the wells that fall within the buffered zone. By displaying these elements, city planners can gain a clear spatial understanding of where the most accessible and potential wells are in relation to the UDZ, which aids in decision-making and planning.

### Summary:
In essence, this code segment aids in identifying and visualizing potential freshwater sources (wells) around San Francisco's UDZ, which is essential for ensuring a consistent water supply for the upcoming infrastructures.


In [ ]:
# Create a buffer around the hexagon boundary
# For this example, we'll buffer by a distance of 0.05 degrees (roughly 5km at the equator)
buffered_hexagon = hexagon.buffer(0.05)

# Perform a spatial join to identify wells that fall within the buffered hexagon
# op='within' checks if the wells (points) are within the buffered hexagon
joined_gdf = gpd.sjoin(gdf, buffered_hexagon, how="inner", op="within")

# Visualization with buffering and the wells within the buffered region
fig, ax = plt.subplots(figsize=(10, 10))
buffered_hexagon.boundary.plot(ax=ax, color='blue', linewidth=1, label='Buffered Hexagon')
hexagon.boundary.plot(ax=ax, color='black', linewidth=1, label='Original Hexagon')
gdf.plot(ax=ax, marker='o', color='red', markersize=5, label='All Wells')
joined_gdf.plot(ax=ax, marker='x', color='green', markersize=100, label='Wells within Buffered Hexagon')
plt.legend(loc="upper left")
plt.show()
